# Visualize and Process CraglistBargains Dataset

In [1]:
import json
from pprint import pprint

In [ ]:
import json
from pprint import pprint

input_file = "raw_data/dev.json"
with open(input_file, 'r') as f:
    dev_data = json.load(f)

In [4]:
pprint(dev_data)

[{'agents': {'0': 'human', '1': 'human'},
  'events': [{'action': 'message',
              'agent': 0,
              'data': 'hi there',
              'start_time': '1496341530.27',
              'time': '1496341531.17'},
             {'action': 'message',
              'agent': 1,
              'data': 'Good Day!',
              'start_time': '1496341541.95',
              'time': '1496341544.09'},
             {'action': 'message',
              'agent': 0,
              'data': 'how are you today?',
              'start_time': '1496341548.5',
              'time': '1496341552.05'},
             {'action': 'message',
              'agent': 1,
              'data': "I'm well. Broke my arm and can't use my go pro for a "
                      'while.',
              'start_time': '1496341568.54',
              'time': '1496341589.53'},
             {'action': 'message',
              'agent': 0,
              'data': 'oh geeze, im sorry to here that. ',
              'start_time': '149

In [50]:
dev_data[100]

{'uuid': 'C_d6959d9d0f924cd3af99446f71cfcc71',
 'scenario': {'category': 'bike',
  'uuid': 'S_5MB9SkJGX0qHz9hD',
  'post_id': '6152159363',
  'kbs': [{'personal': {'Bottomline': None, 'Role': 'buyer', 'Target': 2280},
    'item': {'Category': 'bike',
     'Images': [],
     'Price': 3000,
     'Description': ['I have a 2016 Brand New Neon Spring CAAD12 Hydraulic Disc Brake with full Dura Ace setup that I am selling.  Took it out for one ride (So 30 miles on the bike total).  I was looking for a carbon bike for a long time, and found the bike I wanted right after I purchased this, so I only rode it once.',
      'Frame: CAAD12 Disc, SmartFormed 6069 Alloy, SPEED SAVE, BB30a, Di2 Ready, flat-mount disc',
      'Fork: CAAD12 Disc, SPEED SAVE, BallisTec Carbon, 1-1/8" to 1-1/4", integrated crown race, post-mount disc',
      'Crank: Cannondale HollowGram Si, hollow forged, w/ OPI SpideRing, BB30a, 52/36',
      'Chain: Shimano HG700-11, 11-speed',
      'Rear Derailleur: Shimano Dura-Ace 9

## Get buyer and seller prompt

In [16]:
pprint(dev_data[0]['scenario']['kbs'][0])

{'item': {'Category': 'electronics',
          'Description': ['- HERO4 Black Camera',
                          "- Standard Housing 131' (40m)",
                          '- Rechargeable Battery',
                          '- Flat Adhesive Mount',
                          '- 3-Way Pivot Arm'],
          'Images': ['electronics/6122134540_0.jpg'],
          'Price': 265,
          'Title': 'GoPro Hero4 Black + Battery BacPac'},
 'personal': {'Bottomline': None, 'Role': 'buyer', 'Target': 243}}


In [17]:
pprint(dev_data[0]['scenario']['kbs'][1])

{'item': {'Category': 'electronics',
          'Description': ['- HERO4 Black Camera',
                          "- Standard Housing 131' (40m)",
                          '- Rechargeable Battery',
                          '- Flat Adhesive Mount',
                          '- 3-Way Pivot Arm',
                          '- USB Cable',
                          '- Battery BacPac',
                          '- Battery BacPac case',
                          '- Battery BackPac Backdoor',
                          'NOTE: The only thing missing from a new GoPro Hero4 '
                          'kit is the curved adhesive mount. Everything else '
                          'is included (plus the BacPac kit) in new or like '
                          'new condition.'],
          'Images': ['electronics/6122134540_0.jpg'],
          'Price': 265,
          'Title': 'GoPro Hero4 Black + Battery BacPac'},
 'personal': {'Bottomline': None, 'Role': 'seller', 'Target': 265}}


In [31]:
def get_buyer_seller_info(data_record):
    buyer_dict = data_record['scenario']['kbs'][0]
    assert buyer_dict['personal']['Role'] == 'buyer'
    seller_dict = data_record['scenario']['kbs'][1]
    assert seller_dict['personal']['Role'] == 'seller'
    item_title = buyer_dict['item']['Title']
    item_category = buyer_dict['item']['Category']
    item_list_price = buyer_dict['item']['Price']
    buyer_item_description = buyer_dict['item']['Description'] # a list of strings
    seller_item_description = seller_dict['item']['Description'] # a list of strings
    buyer_target_price = buyer_dict['personal']['Target']
    seller_target_price = seller_dict['personal']['Target']
    assert seller_target_price > buyer_target_price
    return item_title, item_category, item_list_price, {'buyer_item_description': buyer_item_description, 'buyer_target_price':buyer_target_price}, {'seller_item_description':seller_item_description, 'seller_target_price':seller_target_price}

In [32]:
title, category, list_price, buyer_dict, seller_dict = get_buyer_seller_info(dev_data[0])

In [33]:
print(title)
print(category)
print(list_price)
print(buyer_dict)
print(seller_dict)

GoPro Hero4 Black + Battery BacPac
electronics
265
{'buyer_item_description': ['- HERO4 Black Camera', "- Standard Housing 131' (40m)", '- Rechargeable Battery', '- Flat Adhesive Mount', '- 3-Way Pivot Arm'], 'buyer_target_price': 243}
{'seller_item_description': ['- HERO4 Black Camera', "- Standard Housing 131' (40m)", '- Rechargeable Battery', '- Flat Adhesive Mount', '- 3-Way Pivot Arm', '- USB Cable', '- Battery BacPac', '- Battery BacPac case', '- Battery BackPac Backdoor', 'NOTE: The only thing missing from a new GoPro Hero4 kit is the curved adhesive mount. Everything else is included (plus the BacPac kit) in new or like new condition.'], 'seller_target_price': 265}


In [40]:
buyer_item_description = '\n'.join(buyer_dict['buyer_item_description'])
buyer_initial_prompt = f"""
You are a buyer negotiating the purchase of a {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{buyer_item_description}
Your target price is {buyer_dict['buyer_target_price']}, and you aim to negotiate towards this amount.
"""

In [41]:
print(buyer_initial_prompt)


You are a buyer negotiating the purchase of a GoPro Hero4 Black + Battery BacPac.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: electronics
- Listed Price: 265
- Description:
- HERO4 Black Camera
- Standard Housing 131' (40m)
- Rechargeable Battery
- Flat Adhesive Mount
- 3-Way Pivot Arm
Your target price is 243, and you aim to negotiate towards this amount.



In [95]:
def get_buyer_seller_prompt(data_record):
    title, category, list_price, buyer_dict, seller_dict = get_buyer_seller_info(data_record)
    buyer_item_description = '\n'.join(buyer_dict['buyer_item_description'])
    buyer_initial_prompt = f"""You are a buyer negotiating the purchase of a {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{buyer_item_description}
Your target price is {buyer_dict['buyer_target_price']}, and you aim to negotiate towards this amount.
"""

    seller_item_description = '\n'.join(seller_dict['seller_item_description'])
    seller_initial_prompt = f"""You are a seller negotiating the sale of a {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{seller_item_description}
Your target price is {seller_dict['seller_target_price']}, and you aim to negotiate towards this amount.
"""
    return buyer_initial_prompt, seller_initial_prompt

In [96]:
buyer_initial_prompt, seller_initial_prompt = get_buyer_seller_prompt(dev_data[0])
print(buyer_initial_prompt)
print(seller_initial_prompt)

You are a buyer negotiating the purchase of a GoPro Hero4 Black + Battery BacPac.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: electronics
- Listed Price: 265
- Description:
- HERO4 Black Camera
- Standard Housing 131' (40m)
- Rechargeable Battery
- Flat Adhesive Mount
- 3-Way Pivot Arm
Your target price is 243, and you aim to negotiate towards this amount.

You are a seller negotiating the sale of a GoPro Hero4 Black + Battery BacPac.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: electronics
- Listed Price: 265
- Description:
- HERO4 Black Camera
- Standard Housing 131' (40m)
- Rechargeable Battery
- Flat Adhesive Mount
- 3-Way Pivot Arm
- USB Cable
- Battery BacPac
- Battery BacPac case
- Battery BackPac Backdoor
NOTE: The only thing missing

## Get conversation

In [ ]:
for data_record in dev_data:
    print(data_record['events'])

{'reward': 1, 'offer': {'price': 243.0, 'sides': ''}}
{'reward': 0, 'offer': None}
{'reward': 0, 'offer': None}
{'reward': 1, 'offer': {'price': 140.0, 'sides': ''}}
{'reward': 0, 'offer': {'price': 247.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 250.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 38.0, 'sides': ''}}
{'reward': 0, 'offer': None}
{'reward': 0, 'offer': {'price': 12.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 240.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 2000.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 110.0, 'sides': ''}}
{'reward': 0, 'offer': None}
{'reward': 0, 'offer': None}
{'reward': 0, 'offer': {'price': 650.0, 'sides': ''}}
{'reward': 0, 'offer': None}
{'reward': 1, 'offer': {'price': 20.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 1850.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 2000.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 17.0, 'sides': ''}}
{'reward': 1, 'offer': {'price': 105.0, 'sides': ''}}
{'reward': 1, 'of

In [71]:
dev_data[4]['events']

[{'action': 'message',
  'start_time': '1496345145.41',
  'data': 'hello, are you intereste din the bed?',
  'agent': 1,
  'time': '1496345151.73'},
 {'action': 'offer',
  'start_time': None,
  'data': {'price': 247.0, 'sides': ''},
  'agent': 0,
  'time': '1496345161.63'},
 {'action': 'message',
  'start_time': '1496345184.45',
  'data': 'I think 247 is rather low, anychance you can come up?',
  'agent': 1,
  'time': '1496345194.85'},
 {'action': 'message',
  'start_time': '1496345226.39',
  'data': "Perhaps if there are other perks to the item that I don't know about yet.",
  'agent': 0,
  'time': '1496345251.35'},
 {'action': 'message',
  'start_time': '1496345269.66',
  'data': 'well it is very well cared for and also does come with a mattress, both great quality and condition .',
  'agent': 1,
  'time': '1496345296.02'},
 {'action': 'reject',
  'start_time': None,
  'data': None,
  'agent': 1,
  'time': '1496345361.85'}]

In [62]:
def get_sale_price(data_record):
    if data_record['outcome']['reward'] == 1:
        sale_price = data_record['outcome']['offer']['price']
    else:
        sale_price = None
    return sale_price

In [64]:
get_sale_price(dev_data[1]) is None

True

In [ ]:
# possible actions: message, offer, quit, accept, reject

In [ ]:
# define tools for negotiation agents

def make_an_offer(price: float, sides: str) -> str:
    """
    Propose a new offer to the opponent.

    Args:
        price: The price you propose to buy or sell the item, depending on whether you are buyer or seller
        sides: Additional incentives or terms provided to make the offer more attractive (e.g., free shipping, extended warranty).
    Returns:
        A formatted message presenting the offer details to the opponent.
    """
    return f"New Offer Proposed:\n- Price: {price}\n- Side Offer: {sides}"

def accept_the_offer() -> str:
    """
    Accept the current offer from the opponent.
    Returns:
        Confirmation message indicating acceptance of the offer.
    """
    return "Offer Accepted"

def reject_the_offer() -> str:
    """
    Reject the current offer from the opponent.
    Returns:
        Message indicating the offer has been declined.
    """
    return "Offer Rejected"

def quit_conversation() -> str:
    """
    Exit the negotiation and end the conversation.
    Returns:
        Message confirming the conversation has been closed.
    """
    return "Conversation Ended"

In [77]:
def format_event_list(event_list, perspective):
    if perspective == "buyer":
        role_id = 0
    elif perspective == "seller":
        role_id = 1
    else:
        raise ValueError(f"Invalid input perspective: {perspective}")
    # let's now get the data from buyer perspective
    history = []
    for event in event_list:
        if event['agent'] == role_id:
            role = 'assistant'
        else:
            role = 'user'
        
        if event['action'] == 'message':
            history.append({'role':role, 'content':event['data']})
        elif event['action'] == 'offer':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
            else:
                tool_call = {"name": "make_an_offer", "arguments": {"price": event['data']['price'], "sides": event['data']['sides']}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "make_an_offer", "content": f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
        elif event['action'] == 'accept':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Accepted"})
            else:
                tool_call = {"name": "accept_the_offer", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "accept_the_offer", "content": "Offer Accepted"})
        elif event['action'] == 'reject':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Rejected"})
            else:
                tool_call = {"name": "reject_the_offer", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "reject_the_offer", "content": "Offer Rejected"})
        elif event['action'] == 'quit':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Conversation Ended"})
            else:
                tool_call = {"name": "quit_conversation", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "quit_conversation", "content": "Conversation Ended"})
        else:
            raise ValueError(f"Unknown action: {event['action']}")
    return history


In [75]:
dev_data[4]['events']

[{'action': 'message',
  'start_time': '1496345145.41',
  'data': 'hello, are you intereste din the bed?',
  'agent': 1,
  'time': '1496345151.73'},
 {'action': 'offer',
  'start_time': None,
  'data': {'price': 247.0, 'sides': ''},
  'agent': 0,
  'time': '1496345161.63'},
 {'action': 'message',
  'start_time': '1496345184.45',
  'data': 'I think 247 is rather low, anychance you can come up?',
  'agent': 1,
  'time': '1496345194.85'},
 {'action': 'message',
  'start_time': '1496345226.39',
  'data': "Perhaps if there are other perks to the item that I don't know about yet.",
  'agent': 0,
  'time': '1496345251.35'},
 {'action': 'message',
  'start_time': '1496345269.66',
  'data': 'well it is very well cared for and also does come with a mattress, both great quality and condition .',
  'agent': 1,
  'time': '1496345296.02'},
 {'action': 'reject',
  'start_time': None,
  'data': None,
  'agent': 1,
  'time': '1496345361.85'}]

In [79]:
history = format_event_list(dev_data[4]['events'], 'seller')
for event in history:
    print(event)

{'role': 'assistant', 'content': 'hello, are you intereste din the bed?'}
{'role': 'user', 'content': 'New Offer Proposed:\n- Price: 247.0\n- Side Offer: '}
{'role': 'assistant', 'content': 'I think 247 is rather low, anychance you can come up?'}
{'role': 'user', 'content': "Perhaps if there are other perks to the item that I don't know about yet."}
{'role': 'assistant', 'content': 'well it is very well cared for and also does come with a mattress, both great quality and condition .'}
{'role': 'assistant', 'tool_calls': [{'type': 'function', 'function': {'name': 'reject_the_offer', 'arguments': {}}}]}
{'role': 'tool', 'name': 'reject_the_offer', 'content': 'Offer Rejected'}


## Preprocess dataset

In [126]:
def get_buyer_seller_info(data_record):
    buyer_dict = data_record['scenario']['kbs'][0]
    assert buyer_dict['personal']['Role'] == 'buyer'
    seller_dict = data_record['scenario']['kbs'][1]
    assert seller_dict['personal']['Role'] == 'seller'
    item_title = buyer_dict['item']['Title']
    item_category = buyer_dict['item']['Category']
    item_list_price = buyer_dict['item']['Price']
    buyer_item_description = buyer_dict['item']['Description'] # a list of strings
    seller_item_description = seller_dict['item']['Description'] # a list of strings
    buyer_target_price = buyer_dict['personal']['Target']
    seller_target_price = seller_dict['personal']['Target']
    assert seller_target_price > buyer_target_price
    return item_title, item_category, item_list_price, {'buyer_item_description': buyer_item_description, 'buyer_target_price':buyer_target_price}, {'seller_item_description':seller_item_description, 'seller_target_price':seller_target_price}

def get_sale_price(data_record):
    if data_record['outcome']['reward'] == 1:
        sale_price = data_record['outcome']['offer']['price']
    else:
        sale_price = None
    return sale_price

def get_buyer_seller_prompt(data_record):
    title, category, list_price, buyer_dict, seller_dict = get_buyer_seller_info(data_record)
    buyer_item_description = '\n'.join(buyer_dict['buyer_item_description'])
    buyer_initial_prompt = f"""You are a buyer negotiating the purchase of an item titled: {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{buyer_item_description}
Your target price is {buyer_dict['buyer_target_price']}, and you aim to negotiate towards this amount.
"""

    seller_item_description = '\n'.join(seller_dict['seller_item_description'])
    seller_initial_prompt = f"""You are a seller negotiating the sale of an item titled: {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{seller_item_description}
Your target price is {seller_dict['seller_target_price']}, and you aim to negotiate towards this amount.
"""
    return buyer_initial_prompt, seller_initial_prompt

def format_event_list(event_list, perspective):
    if perspective == "buyer":
        role_id = 0
    elif perspective == "seller":
        role_id = 1
    else:
        raise ValueError(f"Invalid input perspective: {perspective}")
    # let's now get the data from buyer perspective
    history = []
    for event in event_list:
        if event['agent'] == role_id:
            role = 'assistant'
        else:
            role = 'user'
        
        if event['action'] == 'message':
            history.append({'role':role, 'content':event['data']})
        elif event['action'] == 'offer':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
            else:
                tool_call = {"name": "make_an_offer", "arguments": {"price": event['data']['price'], "sides": event['data']['sides']}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "make_an_offer", "content": f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
        elif event['action'] == 'accept':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Accepted"})
            else:
                tool_call = {"name": "accept_the_offer", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "accept_the_offer", "content": "Offer Accepted"})
        elif event['action'] == 'reject':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Rejected"})
            else:
                tool_call = {"name": "reject_the_offer", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "reject_the_offer", "content": "Offer Rejected"})
        elif event['action'] == 'quit':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Conversation Ended"})
            else:
                tool_call = {"name": "quit_conversation", "arguments": {}}
                history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                history.append({"role": "tool", "name": "quit_conversation", "content": "Conversation Ended"})
        else:
            raise ValueError(f"Unknown action: {event['action']}")
    return history


In [101]:
data_file = "dev.json"
with open(data_file, 'r') as f:
    data = json.load(f)

In [102]:
data[1]

{'uuid': 'C_1936583922d4472d84268692c2de533e',
 'scenario': {'category': 'housing',
  'uuid': 'S_L7F3EuuCeGp3YW2v',
  'post_id': '6132705525',
  'kbs': [{'personal': {'Bottomline': None, 'Role': 'buyer', 'Target': 1497},
    'item': {'Category': 'housing',
     'Images': ['housing/6132705525_0.jpg'],
     'Price': 2495,
     'Description': ['2131 Hearst Ave, #7',
      'No. of Units on Property: 8',
      'Heat: Steam/Radiator',
      'Windows: Blinds',
      'Laundry: Coin',
      'Pets: Sorry, no pets.',
      'Owner Pays: Hot & Cold Water, Garbage, Sewer, Heat'],
     'Title': 'MUST SEE!! Beautiful new kitchen and bathroom, Great neighborhood!!!'}},
   {'personal': {'Bottomline': None, 'Role': 'seller', 'Target': 2495},
    'item': {'Category': 'housing',
     'Images': ['housing/6132705525_0.jpg'],
     'Price': 2495,
     'Description': ['2131 Hearst Ave, #7',
      'No. of Units on Property: 8',
      'Heat: Steam/Radiator',
      'Windows: Blinds',
      'Laundry: Coin',
      '

In [127]:
def process_data(data_file):
    with open(data_file, 'r') as f:
        data = json.load(f)

    processed_data = []
    for data_record in data:
        # print(data_record)
        # get the system prompt for buyer and seller
        buyer_system_prompt, seller_system_prompt = get_buyer_seller_prompt(data_record)
        sale_price = get_sale_price(data_record)
        buyer_history = format_event_list(data_record['events'], 'buyer')
        seller_history = format_event_list(data_record['events'], 'seller')
        # pprint([{'role': 'system', 'content':buyer_system_prompt}]+buyer_history)
        # pprint([{'role': 'system', 'content':seller_system_prompt}]+seller_history)
        # print("=============")
        processed_data.append({'messages':[{'role': 'system', 'content':buyer_system_prompt}]+buyer_history, 'sale_price':sale_price})
        processed_data.append({'messages':[{'role': 'system', 'content':seller_system_prompt}]+seller_history, 'sale_price':sale_price})
    print(f"number of data records processed: {len(processed_data)/2}")
    return processed_data


In [137]:
processed_data = []
for data_file in ['train.json', 'test.json', 'dev.json']:
    processed_data += process_data(data_file)

print(len(processed_data))

with open("processed_data.json", "w") as file:
    json.dump(processed_data, file, indent=4)

number of data records processed: 5247.0
number of data records processed: 838.0
number of data records processed: 597.0
13364


In [136]:
pprint(processed_data[510])

{'messages': [{'content': 'You are a buyer negotiating the purchase of an item '
                          'titled: Beautiful 1 Bedroom Home with Balcony '
                          'Available Mid June!.\n'
                          'Your objective is to get the best possible deal '
                          'while maintaining a friendly and engaging '
                          'conversation. \n'
                          'You have the following information about the '
                          'item: \n'
                          '- Category: housing\n'
                          '- Listed Price: 2834\n'
                          '- Description:\n'
                          'Essex Property Trust\n'
                          'EMME Apartment Homes\n'
                          '6350 Christie Ave, Emeryville, CA 94608\n'
                          'We will have a 1 bedroom 1 bath 643 sq ft apartment '
                          '#130 available on June 10th! Your beautiful new '
             

In [138]:
with open("processed_data.json", "r") as file:
    processed_data = json.load(file)

In [140]:
pprint(processed_data[510])

{'messages': [{'content': 'You are a buyer negotiating the purchase of an item '
                          'titled: Beautiful 1 Bedroom Home with Balcony '
                          'Available Mid June!.\n'
                          'Your objective is to get the best possible deal '
                          'while maintaining a friendly and engaging '
                          'conversation. \n'
                          'You have the following information about the '
                          'item: \n'
                          '- Category: housing\n'
                          '- Listed Price: 2834\n'
                          '- Description:\n'
                          'Essex Property Trust\n'
                          'EMME Apartment Homes\n'
                          '6350 Christie Ave, Emeryville, CA 94608\n'
                          'We will have a 1 bedroom 1 bath 643 sq ft apartment '
                          '#130 available on June 10th! Your beautiful new '
             

## Process data - no tool version

In [2]:
def get_buyer_seller_info(data_record):
    buyer_dict = data_record['scenario']['kbs'][0]
    assert buyer_dict['personal']['Role'] == 'buyer'
    seller_dict = data_record['scenario']['kbs'][1]
    assert seller_dict['personal']['Role'] == 'seller'
    item_title = buyer_dict['item']['Title']
    item_category = buyer_dict['item']['Category']
    item_list_price = buyer_dict['item']['Price']
    buyer_item_description = buyer_dict['item']['Description'] # a list of strings
    seller_item_description = seller_dict['item']['Description'] # a list of strings
    buyer_target_price = buyer_dict['personal']['Target']
    seller_target_price = seller_dict['personal']['Target']
    assert seller_target_price > buyer_target_price
    return item_title, item_category, item_list_price, {'buyer_item_description': buyer_item_description, 'buyer_target_price':buyer_target_price}, {'seller_item_description':seller_item_description, 'seller_target_price':seller_target_price}

def get_sale_price(data_record):
    if data_record['outcome']['reward'] == 1:
        sale_price = data_record['outcome']['offer']['price']
    else:
        sale_price = None
    return sale_price

def get_buyer_seller_prompt(data_record):
    title, category, list_price, buyer_dict, seller_dict = get_buyer_seller_info(data_record)
    buyer_item_description = '\n'.join(buyer_dict['buyer_item_description'])
    buyer_initial_prompt = f"""You are a buyer negotiating the purchase of an item titled: {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{buyer_item_description}
Your target price is {buyer_dict['buyer_target_price']}, and you aim to negotiate towards this amount.
"""

    seller_item_description = '\n'.join(seller_dict['seller_item_description'])
    seller_initial_prompt = f"""You are a seller negotiating the sale of an item titled: {title}.
Your objective is to get the best possible deal while maintaining a friendly and engaging conversation. 
You have the following information about the item: 
- Category: {category}
- Listed Price: {list_price}
- Description:
{seller_item_description}
Your target price is {seller_dict['seller_target_price']}, and you aim to negotiate towards this amount.
"""
    return buyer_initial_prompt, seller_initial_prompt

def format_event_list(event_list, perspective):
    if perspective == "buyer":
        role_id = 0
    elif perspective == "seller":
        role_id = 1
    else:
        raise ValueError(f"Invalid input perspective: {perspective}")
    # let's now get the data from buyer perspective
    history = []
    for event in event_list:
        if event['agent'] == role_id:
            role = 'assistant'
        else:
            role = 'user'
        
        if event['action'] == 'message':
            history.append({'role':role, 'content':event['data']})
        elif event['action'] == 'offer':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
            else:
                # tool_call = {"name": "make_an_offer", "arguments": {"price": event['data']['price'], "sides": event['data']['sides']}}
                # history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                # history.append({"role": "tool", "name": "make_an_offer", "content": f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
                history.append({'role':role, 'content':f"New Offer Proposed:\n- Price: {event['data']['price']}\n- Side Offer: {event['data']['sides']}"})
        elif event['action'] == 'accept':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Accepted"})
            else:
                # tool_call = {"name": "accept_the_offer", "arguments": {}}
                # history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                # history.append({"role": "tool", "name": "accept_the_offer", "content": "Offer Accepted"})
                history.append({'role':role, 'content':"Offer Accepted"})
        elif event['action'] == 'reject':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Offer Rejected"})
            else:
                # tool_call = {"name": "reject_the_offer", "arguments": {}}
                # history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                # history.append({"role": "tool", "name": "reject_the_offer", "content": "Offer Rejected"})
                history.append({'role':role, 'content':"Offer Rejected"})
        elif event['action'] == 'quit':
            # see whether it is buyer or seller making an offer
            if role == 'user':
                history.append({'role':role, 'content':"Conversation Ended"})
            else:
                # tool_call = {"name": "quit_conversation", "arguments": {}}
                # history.append({"role":role, "tool_calls": [{"type": "function", "function": tool_call}]})
                # history.append({"role": "tool", "name": "quit_conversation", "content": "Conversation Ended"})
                history.append({'role':role, 'content':"Conversation Ended"})
        else:
            raise ValueError(f"Unknown action: {event['action']}")
    return history

def process_data_no_tool(data_file):
    with open(data_file, 'r') as f:
        data = json.load(f)

    processed_data = []
    for data_record in data:
        # print(data_record)
        # get the system prompt for buyer and seller
        buyer_system_prompt, seller_system_prompt = get_buyer_seller_prompt(data_record)
        sale_price = get_sale_price(data_record)
        buyer_history = format_event_list(data_record['events'], 'buyer')
        seller_history = format_event_list(data_record['events'], 'seller')
        # pprint([{'role': 'system', 'content':buyer_system_prompt}]+buyer_history)
        # pprint([{'role': 'system', 'content':seller_system_prompt}]+seller_history)
        # print("=============")
        processed_data.append({'messages':[{'role': 'system', 'content':buyer_system_prompt}]+buyer_history, 'sale_price':sale_price})
        processed_data.append({'messages':[{'role': 'system', 'content':seller_system_prompt}]+seller_history, 'sale_price':sale_price})
    print(f"number of data records processed: {len(processed_data)/2}")
    return processed_data


In [ ]:
processed_data = []
for data_file in ['train.json', 'test.json', 'dev.json']:
    processed_data += process_data_no_tool(data_file)

print(len(processed_data))

number of data records processed: 5247.0
number of data records processed: 838.0
number of data records processed: 597.0
13364


In [9]:
processed_data[0]['messages']

[{'role': 'system',
  'content': 'You are a buyer negotiating the purchase of an item titled: Verizon Car Charger with Dual Output Micro USB and LED Light.\nYour objective is to get the best possible deal while maintaining a friendly and engaging conversation. \nYou have the following information about the item: \n- Category: phone\n- Listed Price: 10\n- Description:\nCharge two devices simultaneously on the go. This vehicle charger with an additional USB port delivers enough power to charge two devices at once. The push-button activated LED connector light means no more fumbling in the dark trying to connect your device. Auto Detect IC Technology automatically detects the device type and its specific charging needs for improved compatibility. And the built-in indicator light illuminates red to let you know the charger is receiving power and the power socket is working properly.\nYour target price is 7, and you aim to negotiate towards this amount.\n'},
 {'role': 'assistant',
  'conten

In [10]:
with open("processed_data_no_tool.json", "w") as file:
    json.dump(processed_data, file, indent=4)

In [11]:
with open("processed_data_no_tool.json", "r") as file:
    processed_data_no_tool = json.load(file)

In [13]:
pprint(processed_data[100])

{'messages': [{'content': 'You are a buyer negotiating the purchase of an item '
                          'titled: Long board custom bilt from the board up.\n'
                          'Your objective is to get the best possible deal '
                          'while maintaining a friendly and engaging '
                          'conversation. \n'
                          'You have the following information about the '
                          'item: \n'
                          '- Category: bike\n'
                          '- Listed Price: 200\n'
                          '- Description:\n'
                          'Hey there cl I have a long board for sale pretty '
                          'much brand knew rode all together 4 or 5 times . '
                          'The brand on the deck is a gravity skateboard. The '
                          'brand of trucks are sidewinder 2sGuwuing.mini '
                          'monster hawgs 70mm 78a Wheels with Swiss bones '
      